# Scraping Code

## Libraries

In [1]:
import json
import time
import pandas as pd
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import TimeoutException
from selenium.webdriver.common.action_chains import ActionChains
from bs4 import BeautifulSoup
import cloudinary
import cloudinary.uploader

## Functions

In [2]:
def scroll_to_bottom(increment=3000, pause_time=1):
    while True:
        last_position = driver.execute_script("return window.pageYOffset;")
        driver.execute_script(f"window.scrollBy(0, {increment});")
        time.sleep(pause_time)
        new_position = driver.execute_script("return window.pageYOffset;")

        if new_position == last_position:
            break

def get_module_data():
    
    print("Collecting module links from the search page...")
    module_data = []
    box_modules = driver.find_elements(By.CLASS_NAME, "box-module")

    for module in box_modules:
        try:
            module_id = module.get_attribute("data-module-id")
            link_element = module.find_element(By.TAG_NAME, "a")
            href = link_element.get_attribute("href")

            if href.startswith("https"):
                print(f"Found module ID {module_id} with link {href}")
                module_data.append({"id": module_id, "link": href})
        except Exception as e:
            print("No link found in this module:", e)

    print("Total modules found:", len(module_data))
    return module_data

def scrape_page(module_info, wait, driver):
    url = module_info['link']
    module_id = module_info['id']
    
    # Initialize results with default values
    results = {
        "id": module_id,
        "module_name": None,
        "manufacturer": None,
        "primary_desc": None,
        "available": None,
        "approved_stamp": None,
        "physical_dim": None,
        "power_req": None,
        "module_tags": None,
        "full_desc": None,
        "price_in_euro": None,
        "price_in_dollar": None,
        "module_url": url,
        "cloudinary_url": None
    }
    
    try: 
        wait.until(EC.presence_of_element_located((By.CSS_SELECTOR, ".module-view-header h1")))
    except Exception as e:
        print(f"Timeout waiting for module name on {url}: {e}")
    
    # --------------------------------------- MODULE NAME ---------------------------------------
    try:
        module_name_element = driver.find_element(By.CSS_SELECTOR, ".module-view-header h1")
        results["module_name"] = module_name_element.text.strip()
    except Exception as e:
        print(f"Module name not found for {url}: {e}")
        results["module_name"] = ""
    
    # --------------------------------------- MANUFACTURER ---------------------------------------
    try: 
        manufacturer_element = driver.find_element(By.CSS_SELECTOR, ".vendor-name")
        results["manufacturer"] = manufacturer_element.text.strip()
    except Exception as e:
        print(f"Manufacturer not found for {url}: {e}")
        results["manufacturer"] = ""
    
    # --------------------------------------- PRIMARY DESCRIPTION ---------------------------------------
    try:
        primary_description_element = driver.find_element(By.CSS_SELECTOR, "p.lead.wrap")
        results["primary_desc"] = primary_description_element.text.strip()
    except Exception as e:
        print(f"Primary description not found for {url}: {e}")
        results["primary_desc"] = ""
    
    # --------------------------------------- AVAILABILITY ---------------------------------------
    try: 
        availability_elements = driver.find_elements(
            By.XPATH, 
            "//div[contains(@class, 'subspec')]/p[contains(@class, 'text-success') and contains(., 'currently available')]"
        )
        results["available"] = 1 if availability_elements else 0
    except Exception as e:
        print(f"Error determining availability for {url}: {e}")
        results["available"] = 0
    
    # --------------------------------------- APPROVED STAMP ---------------------------------------
    try:
        driver.find_element(By.CSS_SELECTOR, ".box-approved")
        results["approved_stamp"] = 1
    except Exception:
        results["approved_stamp"] = 0
    
    # --------------------------------------- PHYSICAL DIMENSIONS ---------------------------------------
    try:
        dims_dt = driver.find_element(By.XPATH, "//dt[normalize-space(text())='Dimensions']")
        parent_dl = dims_dt.find_element(By.XPATH, "./..")
        dd_elements = parent_dl.find_elements(By.TAG_NAME, "dd")
        dimensions_list = [dd.text.strip() for dd in dd_elements if dd.text.strip()]
        results["physical_dim"] = " | ".join(dimensions_list)
    except Exception as e:
        print(f"Dimensions not found for {url}: {e}")
        results["physical_dim"] = ""
    
    # --------------------------------------- POWER REQUIREMENTS ---------------------------------------
    try:
        current_draw_dt = driver.find_element(By.XPATH, "//dt[contains(., 'Current') and contains(., 'Draw')]")
        parent_dl = current_draw_dt.find_element(By.XPATH, "./..")
        dd_elements = parent_dl.find_elements(By.TAG_NAME, "dd")
        current_draw_list = [dd.text.strip() for dd in dd_elements if dd.text.strip()]
        results["power_req"] = " | ".join(current_draw_list)
    except Exception as e:
        print(f"Power requirements not found for {url}: {e}") 
        results["power_req"] = ""
    
    # --------------------------------------- MODULE TAGS ---------------------------------------
    try:
        tags_div = driver.find_element(By.CSS_SELECTOR, "div.module-tags")
        tag_spans = tags_div.find_elements(By.CSS_SELECTOR, "span.label")
        results["module_tags"] = ", ".join([span.text.strip() for span in tag_spans if span.text.strip()])
    except Exception as e:
        print(f"Module tags not found for {url}: {e}")
        results["module_tags"] = ""
    
    # --------------------------------------- FULL DESCRIPTION ---------------------------------------
    try:
        module_details_div = driver.find_element(By.ID, "module-details")
        p_elements = module_details_div.find_elements(By.TAG_NAME, "p")
        full_desc_paragraphs = []
        for p in p_elements:
            p_classes = p.get_attribute("class") or ""
            if "lead" in p_classes and "wrap" in p_classes:
                continue
            if p.find_elements(By.TAG_NAME, "a"):
                continue
            text = p.text.strip()
            if text:
                full_desc_paragraphs.append(text)
        results["full_desc"] = "\n".join(full_desc_paragraphs)
    except Exception as e:
        print(f"Full description not found for {url}: {e}")
        results["full_desc"] = ""
    
    # --------------------------------------- PRICING INFORMATION (EURO) ---------------------------------------
    try:
        price_dd = driver.find_element(By.XPATH, "//dt[normalize-space(text())='Price']/following-sibling::dd")
        price_spans = price_dd.find_elements(By.XPATH, ".//span[contains(@class, 'currency-approx') or contains(@class, 'currency')]")
        price_texts = []
        for span in price_spans:
            text = span.text.strip()
            classes = span.get_attribute("class")
            if "currency-approx" in classes:
                text = "≈" + text
            price_texts.append(text)
        results["price_in_euro"] = " | ".join(price_texts)
    except Exception as e:
        print(f"Euro price not found for {url}: {e}")
        results["price_in_euro"] = ""
    
    # --------------------------------------- SWITCH TO USD AND SCRAPE PRICING ---------------------------------------
    try:
        usd_link = wait.until(EC.element_to_be_clickable((By.XPATH, "//a[contains(@title, 'Display prices in $')]")))
        driver.execute_script("arguments[0].scrollIntoView();", usd_link)
        driver.execute_script("arguments[0].click();", usd_link)
        wait.until(lambda d: "$" in d.find_element(By.XPATH, "//dt[normalize-space(text())='Price']/following-sibling::dd").text)
        price_dd_usd = driver.find_element(By.XPATH, "//dt[normalize-space(text())='Price']/following-sibling::dd")
        price_spans_usd = price_dd_usd.find_elements(By.XPATH, ".//span[contains(@class, 'currency-approx') or contains(@class, 'currency')]")
        price_texts_usd = []
        for span in price_spans_usd:
            text = span.text.strip()
            classes = span.get_attribute("class")
            if "currency-approx" in classes:
                text = "≈" + text
            price_texts_usd.append(text)
        results["price_in_dollar"] = " | ".join(price_texts_usd)
    except Exception as e:
        print(f"Dollar price not found for {url}: {e}")
        results["price_in_dollar"] = ""
    
    # --------------------------------------- REVERT TO EURO CURRENCY ---------------------------------------
    try:
        euro_link = wait.until(EC.element_to_be_clickable((By.XPATH, "//a[contains(@title, 'Display prices in €')]")))
        driver.execute_script("arguments[0].scrollIntoView();", euro_link)
        driver.execute_script("arguments[0].click();", euro_link)
        wait.until(lambda d: "€" in d.find_element(By.XPATH, "//dt[normalize-space(text())='Price']/following-sibling::dd").text)
    except Exception as e:
        print(f"Could not click to display Euro prices for {url}: {e}")
    
    # --------------------------------------- IMAGE EXTRACTION AND UPLOAD ---------------------------------------
    try:
        g_image_div = driver.find_element(By.CLASS_NAME, "g-image")
        a_tag = g_image_div.find_element(By.TAG_NAME, "a")
        relative_image_url = a_tag.get_attribute("href")
        if relative_image_url.startswith("/"):
            base_url = "https://modulargrid.net/"
            full_image_url = base_url + relative_image_url
        else:
            full_image_url= relative_image_url
        upload_result = cloudinary.uploader.upload(full_image_url)
        results["cloudinary_url"] = upload_result.get("secure_url", "")
    except Exception as e:
        print(f"Error uploading image for {url}: {e}")
        results["cloudinary_url"] = ""
    
    print(f"Finished scraping module ID {module_id}\n")
    return results

## Cloudinary Configuration

In [3]:
cloudinary.config(
    cloud_name = "dglh7onu3",
    api_key = "115324728487844",
    api_secret = "68taYQlneJG-JU2izvZsOY3L8sk"
)

## Scraping

In [4]:
print("Setting up Webdriver and navigating to the search URL...")
chrome_options = Options()
#chrome_options.add_argument("--headless") # comment this out if you want to see the browser being controlled by the code
driver = webdriver.Chrome(options=chrome_options)

Setting up Webdriver and navigating to the search URL...


In [7]:
BASE_URL = "https://modulargrid.net"
SEARCH_URL_AVAILABLE = (
    "https://modulargrid.net/e/modules/browser?"
    "SearchName=&SearchVendor=&SearchFunction=&SearchSecondaryfunction=&SearchHeight=&SearchTe=&"
    "SearchTemethod=max&SearchBuildtype=a&SearchLifecycle=available&SearchSet=&SearchMarketplace=&"
    "SearchIsmodeled=0&SearchShowothers=0&SearchShowpanel=0&order=newest&direction=asc"
)

wait = WebDriverWait(driver, 3)

driver.get(SEARCH_URL_AVAILABLE)
time.sleep(3)

time.sleep(2)

try:
    alphabetic_button = driver.find_element(By.CSS_SELECTOR, "a[data-search-order='alphabetic']")
    alphabetic_button.click()
    time.sleep(2)
    
except Exception as e:
    print("Alphabetic sort button not found or click failed:", e)


ITEM_SELECTOR = ".box-module"

SCROLL_PAUSE_TIME = 1

scroll_to_bottom(increment=2000, pause_time=SCROLL_PAUSE_TIME)

elements = driver.find_elements(By.CSS_SELECTOR, ITEM_SELECTOR)
print(f"Scrolling complete. Total items found: {len(elements)}")

module_data = get_module_data()

available = []
skipped_urls = []

total_links = len(module_data)

driver.set_page_load_timeout(10)

for idx, module_info in enumerate(module_data, start=1):
    url = module_info['link']
    print(f"Processing link {idx} of {total_links}: {url}")

    try:
        driver.get(url)
    except TimeoutException:
        print(f"Skipping {url} due to timeout")
        skipped_urls.append(module_info)
        continue

    result = scrape_page(module_info, wait, driver)
    if result is None:
        print(f"Warning: Scrape function returned None for {module_info}")
    else:
        available.append(result)

print("\nScraping complete.")
print(f"Total modules processed: {len(available)}")
print(f"Number of originally skipped URLs: {len(skipped_urls)}")

Scrolling complete. Total items found: 7703
Found module ID 24577 with link https://modulargrid.net/e/paratek-%D0%A0%D0%98%D0%A2%D0%9C%D0%98%D0%9A%D0%A1-aluminium
Found module ID 24578 with link https://modulargrid.net/e/paratek-%D0%A0%D0%98%D0%A2%D0%9C%D0%98%D0%9A%D0%A1-black
Found module ID 26787 with link https://modulargrid.net/e/paratek-%D0%A0%D0%98%D0%A2%D0%9C%D0%98%D0%9A%D0%A1-black--
Found module ID 26788 with link https://modulargrid.net/e/paratek-%D0%A0%D0%98%D0%A2%D0%9C%D0%98%D0%9A%D0%A1-black-pink
Found module ID 29024 with link https://modulargrid.net/e/orpho-8-step
Found module ID 37431 with link https://modulargrid.net/e/synthrotek-adapt-1-4
Found module ID 12311 with link https://modulargrid.net/e/addac-system-addac812vu
Found module ID 51117 with link https://modulargrid.net/e/after-later-audio-ffs
Found module ID 26539 with link https://modulargrid.net/e/error-instruments-indian-resonator-v2
Found module ID 46869 with link https://modulargrid.net/e/apollo-view-modular

In [9]:
available_df = pd.DataFrame(available)
available_df

id               module_name       manufacturer   
0     24577      "РИТМИКС"  aluminium            Paratek  \
1     24578          "РИТМИКС"  black            Paratek   
2     26787          "РИТМИКС"  black            Paratek   
3     26788   "РИТМИКС"  black (pink)            Paratek   
4     29024                    8-Step              Orpho   
...     ...                       ...                ...   
7633  49024  イセーニン (ISE-NIN) BREAKOUT  Black Corporation   
7634  41287     イセーニン (ISE-NIN) VOICE  Black Corporation   
7635  52485            ステージズ (STAGES)        Big T Music   
7636  43075              ベールズ (VEILS)        Big T Music   
7637  46703         ミキシング  mikishingu    Bizarre Jezabel   

                                        primary_desc  available   
0                              8 channels mixer unit          1  \
1                              8 channels mixer unit          1   
2                              8 channels mixer unit          1   
3                              8 channels mixer unit          1   
4                                  TRIGGER SEQUENCER          1   
...                                              ...        ...   
7633                                                          1   
7634                    Monophonic イセーニン Synth Voice          1   
7635      1:1 Replica of Mutable Instruments' Stages          1   
7636  1:1 Replicant of Mutable Instruments' Veils V2          1   
7637                   Four channel mixer / lpg /vca          1   

      approved_stamp        physical_dim                          power_req   
0                  1  12 HP | 38 mm deep   40 mA +12V | 5 mA -12V | ? mA 5V  \
1                  1  12 HP | 38 mm deep   40 mA +12V | 5 mA -12V | ? mA 5V   
2                  1  12 HP | 38 mm deep   40 mA +12V | 5 mA -12V | ? mA 5V   
3                  1  12 HP | 38 mm deep   40 mA +12V | 5 mA -12V | ? mA 5V   
4                  0   6 HP | 35 mm deep   50 mA +12V | ? mA -12V | ? mA 5V   
...              ...                 ...                                ...   
7633               0               22 HP    ? mA +12V | ? mA -12V | ? mA 5V   
7634               0               36 HP    ? mA +12V | ? mA -12V | ? mA 5V   
7635               0  14 HP | 25 mm deep  80 mA +12V | 20 mA -12V | 0 mA 5V   
7636               0  10 HP | 25 mm deep  50 mA +12V | 50 mA -12V | 0 mA 5V   
7637               1   4 HP | 40 mm deep  40 mA +12V | 10 mA -12V | 0 mA 5V   

                                            module_tags   
0               Attenuator, Dual/Stereo, Mixer, Panning  \
1     Attenuator, Dual/Stereo, Mixer, Multiple, Panning   
2     Attenuator, Dual/Stereo, Mixer, Multiple, Panning   
3     Attenuator, Dual/Stereo, Mixer, Multiple, Panning   
4                                             Sequencer   
...                                                 ...   
7633                                           Expander   
7634                                        Synth Voice   
7635  CV Modulation, Envelope Generator, LFO, Sample...   
7636              Attenuator, Mixer, Quad, Utility, VCA   
7637           Mixer, Low Pass Gate, Quad, VCA, Utility   

                                              full_desc price_in_euro   
0     • 8 independent mono channels for audio signal...         ≈€260  \
1     • 8 independent mono channels for audio signal...         ≈€260   
2     • 8 independent mono channels for audio signal...         ≈€260   
3     • 8 independent mono channels for audio signal...         ≈€260   
4     The Orpho 8-Step is an eight-step sequencer wi...           €85   
...                                                 ...           ...   
7633  UNPRECEDENTED PATCHABILITY WHEN YOU WANT IT\nS...         ≈€256   
7634  イセーニン (ISE-NIN, pronounced ee-seh-nin) VOICE b...         ≈€900   
7635  ステージズ is a 1:1 replicant, hand built by Big T ...         ≈€296   
7636  ベールズ is a 1:1 Replicant, hand built by Gareth ...         ≈€164   
7637  Four channel mix

In [15]:
available_df['product_lifecycle'] = 'Currently Available'

In [16]:
available_df

id               module_name       manufacturer   
0     24577      "РИТМИКС"  aluminium            Paratek  \
1     24578          "РИТМИКС"  black            Paratek   
2     26787          "РИТМИКС"  black            Paratek   
3     26788   "РИТМИКС"  black (pink)            Paratek   
4     29024                    8-Step              Orpho   
...     ...                       ...                ...   
7633  49024  イセーニン (ISE-NIN) BREAKOUT  Black Corporation   
7634  41287     イセーニン (ISE-NIN) VOICE  Black Corporation   
7635  52485            ステージズ (STAGES)        Big T Music   
7636  43075              ベールズ (VEILS)        Big T Music   
7637  46703         ミキシング  mikishingu    Bizarre Jezabel   

                                        primary_desc  available   
0                              8 channels mixer unit          1  \
1                              8 channels mixer unit          1   
2                              8 channels mixer unit          1   
3                              8 channels mixer unit          1   
4                                  TRIGGER SEQUENCER          1   
...                                              ...        ...   
7633                                                          1   
7634                    Monophonic イセーニン Synth Voice          1   
7635      1:1 Replica of Mutable Instruments' Stages          1   
7636  1:1 Replicant of Mutable Instruments' Veils V2          1   
7637                   Four channel mixer / lpg /vca          1   

      approved_stamp        physical_dim                          power_req   
0                  1  12 HP | 38 mm deep   40 mA +12V | 5 mA -12V | ? mA 5V  \
1                  1  12 HP | 38 mm deep   40 mA +12V | 5 mA -12V | ? mA 5V   
2                  1  12 HP | 38 mm deep   40 mA +12V | 5 mA -12V | ? mA 5V   
3                  1  12 HP | 38 mm deep   40 mA +12V | 5 mA -12V | ? mA 5V   
4                  0   6 HP | 35 mm deep   50 mA +12V | ? mA -12V | ? mA 5V   
...              ...                 ...                                ...   
7633               0               22 HP    ? mA +12V | ? mA -12V | ? mA 5V   
7634               0               36 HP    ? mA +12V | ? mA -12V | ? mA 5V   
7635               0  14 HP | 25 mm deep  80 mA +12V | 20 mA -12V | 0 mA 5V   
7636               0  10 HP | 25 mm deep  50 mA +12V | 50 mA -12V | 0 mA 5V   
7637               1   4 HP | 40 mm deep  40 mA +12V | 10 mA -12V | 0 mA 5V   

                                            module_tags   
0               Attenuator, Dual/Stereo, Mixer, Panning  \
1     Attenuator, Dual/Stereo, Mixer, Multiple, Panning   
2     Attenuator, Dual/Stereo, Mixer, Multiple, Panning   
3     Attenuator, Dual/Stereo, Mixer, Multiple, Panning   
4                                             Sequencer   
...                                                 ...   
7633                                           Expander   
7634                                        Synth Voice   
7635  CV Modulation, Envelope Generator, LFO, Sample...   
7636              Attenuator, Mixer, Quad, Utility, VCA   
7637           Mixer, Low Pass Gate, Quad, VCA, Utility   

                                              full_desc price_in_euro   
0     • 8 independent mono channels for audio signal...         ≈€260  \
1     • 8 independent mono channels for audio signal...         ≈€260   
2     • 8 independent mono channels for audio signal...         ≈€260   
3     • 8 independent mono channels for audio signal...         ≈€260   
4     The Orpho 8-Step is an eight-step sequencer wi...           €85   
...                                                 ...           ...   
7633  UNPRECEDENTED PATCHABILITY WHEN YOU WANT IT\nS...         ≈€256   
7634  イセーニン (ISE-NIN, pronounced ee-seh-nin) VOICE b...         ≈€900   
7635  ステージズ is a 1:1 replicant, hand built by Big T ...         ≈€296   
7636  ベールズ is a 1:1 Replicant, hand built by Gareth ...         ≈€164   
7637  Four channel mix

In [10]:
available_df.to_csv("currently_available.csv", index = False)

In [12]:
SEARCH_URL_DISCONTINUED = (
    "https://modulargrid.net/e/modules/browser?"
    "SearchName=&SearchVendor=&SearchFunction=&SearchSecondaryfunction=&SearchHeight=&SearchTe=&"
    "SearchTemethod=max&SearchBuildtype=a&SearchLifecycle=discontinued&SearchSet=&SearchMarketplace=&"
    "SearchIsmodeled=0&SearchShowothers=0&SearchShowpanel=0&order=newest&direction=asc"
)

wait = WebDriverWait(driver, 3)

driver.get(SEARCH_URL_DISCONTINUED)
time.sleep(3)

time.sleep(2)

try:
    alphabetic_button = driver.find_element(By.CSS_SELECTOR, "a[data-search-order='alphabetic']")
    alphabetic_button.click()
    time.sleep(2)
    
except Exception as e:
    print("Alphabetic sort button not found or click failed:", e)


ITEM_SELECTOR = ".box-module"

SCROLL_PAUSE_TIME = 2

scroll_to_bottom(increment=2000, pause_time=SCROLL_PAUSE_TIME)

elements = driver.find_elements(By.CSS_SELECTOR, ITEM_SELECTOR)
print(f"Scrolling complete. Total items found: {len(elements)}")

module_data_discontinued = get_module_data()

discontinued = []
skipped_urls_discontinued = []

total_links_discontinued = len(module_data_discontinued)

driver.set_page_load_timeout(10)

for idx, module_info in enumerate(module_data_discontinued, start=1):
    url = module_info['link']
    print(f"Processing link {idx} of {total_links_discontinued}: {url}")

    try:
        driver.get(url)
    except TimeoutException:
        print(f"Skipping {url} due to timeout")
        skipped_urls.append(module_info)
        continue

    result = scrape_page(module_info, wait, driver)
    if result is None:
        print(f"Warning: Scrape function returned None for {module_info}")
    else:
        discontinued.append(result)

print("\nScraping complete.")
print(f"Total modules processed: {len(discontinued)}")
print(f"Number of originally skipped URLs: {len(skipped_urls_discontinued)}")

Scrolling complete. Total items found: 1663
Found module ID 31401 with link https://modulargrid.net/e/razmasynth-cthulhu-2nd-run-w-green-panel
Found module ID 18073 with link https://modulargrid.net/e/intellijel-%C2%B5midi-1u-
Found module ID 26782 with link https://modulargrid.net/e/paratek-5-10-aluminium
Found module ID 26781 with link https://modulargrid.net/e/paratek-5-10-black
Found module ID 33739 with link https://modulargrid.net/e/paratek-saturn-complex-digital-noise-source
Found module ID 24121 with link https://modulargrid.net/e/livestock-electronics-black-bang
Found module ID 24123 with link https://modulargrid.net/e/livestock-electronics-black-felix
Found module ID 24120 with link https://modulargrid.net/e/livestock-electronics-black-maze
Found module ID 24122 with link https://modulargrid.net/e/livestock-electronics-black-mir
Found module ID 18618 with link https://modulargrid.net/e/dovemans-0-sugar
Found module ID 28729 with link https://modulargrid.net/e/g-storm-electro-

In [13]:
discontinued_df = pd.DataFrame(discontinued)
discontinued_df

id                            module_name manufacturer   
0     31401       Cthulhu (2nd run w. Green panel)   Razmasynth  \
1     18073                               µMIDI 1U   Intellijel   
2     26782                       "5-10" aluminium      Paratek   
3     26781                           "5-10" black      Paratek   
4     33739  "SATURN" complex digital noise source      Paratek   
...     ...                                    ...          ...   
1646  20853                  ТАКТОМЕR-2c aluminium      Paratek   
1647  21301                      ТАКТОМЕR-2c black      Paratek   
1648  20854                            ТАКТОМЕR-2д      Paratek   
1649  21291                      ТАКТОМЕR-2д black      Paratek   
1650  16926                          Улучscheisseр       Svarog   

                                           primary_desc  available   
0                                                                0  \
1                                                                0   
2                            4 channel CV signal scaler          0   
3                            4 channel CV signal scaler          0   
4     Сomplex noise generator based on "paradoxical ...          0   
...                                                 ...        ...   
1646                     Gate counter, clock, stopwatch          0   
1647                     Gate counter, clock, stopwatch          0   
1648                     Gate counter, clock, stopwatch          0   
1649                     Gate counter, clock, stopwatch          0   
1650                                   то что вам надо!          0   

      approved_stamp       physical_dim                          power_req   
0                  0              14 HP    ? mA +12V | ? mA -12V | ? mA 5V  \
1                  1              22 HP   47 mA +12V | 3 mA -12V | 0 mA 5V   
2                  1  2 HP | 40 mm deep    ? mA +12V | ? mA -12V | ? mA 5V   
3                  1  2 HP | 40 mm deep    ? mA +12V | ? mA -12V | ? mA 5V   
4                  1  8 HP | 24 mm deep  60 mA +12V | 20 mA -12V | 0 mA 5V   
...              ...                ...                                ...   
1646               1  6 HP | 43 mm deep  180 mA +12V | 0 mA -12V | 0 mA 5V   
1647               1  6 HP | 43 mm deep  180 mA +12V | ? mA -12V | ? mA 5V   
1648               1  6 HP | 32 mm deep  180 mA +12V | 0 mA -12V | 0 mA 5V   
1649               1  6 HP | 32 mm deep  180 mA +12V | ? mA -12V | ? mA 5V   
1650               0  10 HP | 2 mm deep    ? mA +12V | ? mA -12V | ? mA 5V   

                                            module_tags   
0                             Filter, Noise, Oscillator  \
1                                                  MIDI   
2                                               Utility   
3                                               Utility   
4     Clock Generator, Comparator, CV Modulation, Di...   
...                                                 ...   
1646                     Tube, Utility, Clock Generator   
1647                     Tube, Utility, Clock Generator   
1648                     Tube, Utility, Clock Generator   
1649                     Tube, Utility, Clock Generator   
1650                    Dynamics, Effect, Tube, Utility   

                                              full_desc price_in_euro   
0     2 pole filter with ribbon controlled sound gen...                \
1                                                               ≈€124   
2     Unit accurately scales the incoming CV 0-5V si...          ≈€80   
3     Unit accurately scales the incoming CV 0-5V si...          ≈€80   
4     • 4 square generators with very wide range\n• ...         ≈€300   
...                                                 ...           ...   
1646  • eurorack format 2-digit counter of incoming ...         ≈€160   
1647  • eurorack format 2-digit counter of incoming ...         ≈€160   
1648  • eurorack format 2-digit counter of incoming ...     

In [17]:
discontinued_df['product_lifecycle'] = "Discontinued"

In [18]:
discontinued_df

id                            module_name manufacturer   
0     31401       Cthulhu (2nd run w. Green panel)   Razmasynth  \
1     18073                               µMIDI 1U   Intellijel   
2     26782                       "5-10" aluminium      Paratek   
3     26781                           "5-10" black      Paratek   
4     33739  "SATURN" complex digital noise source      Paratek   
...     ...                                    ...          ...   
1646  20853                  ТАКТОМЕR-2c aluminium      Paratek   
1647  21301                      ТАКТОМЕR-2c black      Paratek   
1648  20854                            ТАКТОМЕR-2д      Paratek   
1649  21291                      ТАКТОМЕR-2д black      Paratek   
1650  16926                          Улучscheisseр       Svarog   

                                           primary_desc  available   
0                                                                0  \
1                                                                0   
2                            4 channel CV signal scaler          0   
3                            4 channel CV signal scaler          0   
4     Сomplex noise generator based on "paradoxical ...          0   
...                                                 ...        ...   
1646                     Gate counter, clock, stopwatch          0   
1647                     Gate counter, clock, stopwatch          0   
1648                     Gate counter, clock, stopwatch          0   
1649                     Gate counter, clock, stopwatch          0   
1650                                   то что вам надо!          0   

      approved_stamp       physical_dim                          power_req   
0                  0              14 HP    ? mA +12V | ? mA -12V | ? mA 5V  \
1                  1              22 HP   47 mA +12V | 3 mA -12V | 0 mA 5V   
2                  1  2 HP | 40 mm deep    ? mA +12V | ? mA -12V | ? mA 5V   
3                  1  2 HP | 40 mm deep    ? mA +12V | ? mA -12V | ? mA 5V   
4                  1  8 HP | 24 mm deep  60 mA +12V | 20 mA -12V | 0 mA 5V   
...              ...                ...                                ...   
1646               1  6 HP | 43 mm deep  180 mA +12V | 0 mA -12V | 0 mA 5V   
1647               1  6 HP | 43 mm deep  180 mA +12V | ? mA -12V | ? mA 5V   
1648               1  6 HP | 32 mm deep  180 mA +12V | 0 mA -12V | 0 mA 5V   
1649               1  6 HP | 32 mm deep  180 mA +12V | ? mA -12V | ? mA 5V   
1650               0  10 HP | 2 mm deep    ? mA +12V | ? mA -12V | ? mA 5V   

                                            module_tags   
0                             Filter, Noise, Oscillator  \
1                                                  MIDI   
2                                               Utility   
3                                               Utility   
4     Clock Generator, Comparator, CV Modulation, Di...   
...                                                 ...   
1646                     Tube, Utility, Clock Generator   
1647                     Tube, Utility, Clock Generator   
1648                     Tube, Utility, Clock Generator   
1649                     Tube, Utility, Clock Generator   
1650                    Dynamics, Effect, Tube, Utility   

                                              full_desc price_in_euro   
0     2 pole filter with ribbon controlled sound gen...                \
1                                                               ≈€124   
2     Unit accurately scales the incoming CV 0-5V si...          ≈€80   
3     Unit accurately scales the incoming CV 0-5V si...          ≈€80   
4     • 4 square generators with very wide range\n• ...         ≈€300   
...                                                 ...           ...   
1646  • eurorack format 2-digit counter of incoming ...         ≈€160   
1647  • eurorack format 2-digit counter of incoming ...         ≈€160   
1648  • eurorack format 2-digit counter of incoming ...     

In [14]:
discontinued_df.to_csv("discontinued.csv", index = False)

In [19]:
data = pd.concat([available_df, discontinued_df], ignore_index=True)
data

id              module_name manufacturer   
0     24577     "РИТМИКС"  aluminium      Paratek  \
1     24578         "РИТМИКС"  black      Paratek   
2     26787         "РИТМИКС"  black      Paratek   
3     26788  "РИТМИКС"  black (pink)      Paratek   
4     29024                   8-Step        Orpho   
...     ...                      ...          ...   
9284  20853    ТАКТОМЕR-2c aluminium      Paratek   
9285  21301        ТАКТОМЕR-2c black      Paratek   
9286  20854              ТАКТОМЕR-2д      Paratek   
9287  21291        ТАКТОМЕR-2д black      Paratek   
9288  16926            Улучscheisseр       Svarog   

                        primary_desc  available  approved_stamp   
0              8 channels mixer unit          1               1  \
1              8 channels mixer unit          1               1   
2              8 channels mixer unit          1               1   
3              8 channels mixer unit          1               1   
4                  TRIGGER SEQUENCER          1               0   
...                              ...        ...             ...   
9284  Gate counter, clock, stopwatch          0               1   
9285  Gate counter, clock, stopwatch          0               1   
9286  Gate counter, clock, stopwatch          0               1   
9287  Gate counter, clock, stopwatch          0               1   
9288                то что вам надо!          0               0   

            physical_dim                          power_req   
0     12 HP | 38 mm deep   40 mA +12V | 5 mA -12V | ? mA 5V  \
1     12 HP | 38 mm deep   40 mA +12V | 5 mA -12V | ? mA 5V   
2     12 HP | 38 mm deep   40 mA +12V | 5 mA -12V | ? mA 5V   
3     12 HP | 38 mm deep   40 mA +12V | 5 mA -12V | ? mA 5V   
4      6 HP | 35 mm deep   50 mA +12V | ? mA -12V | ? mA 5V   
...                  ...                                ...   
9284   6 HP | 43 mm deep  180 mA +12V | 0 mA -12V | 0 mA 5V   
9285   6 HP | 43 mm deep  180 mA +12V | ? mA -12V | ? mA 5V   
9286   6 HP | 32 mm deep  180 mA +12V | 0 mA -12V | 0 mA 5V   
9287   6 HP | 32 mm deep  180 mA +12V | ? mA -12V | ? mA 5V   
9288   10 HP | 2 mm deep    ? mA +12V | ? mA -12V | ? mA 5V   

                                            module_tags   
0               Attenuator, Dual/Stereo, Mixer, Panning  \
1     Attenuator, Dual/Stereo, Mixer, Multiple, Panning   
2     Attenuator, Dual/Stereo, Mixer, Multiple, Panning   
3     Attenuator, Dual/Stereo, Mixer, Multiple, Panning   
4                                             Sequencer   
...                                                 ...   
9284                     Tube, Utility, Clock Generator   
9285                     Tube, Utility, Clock Generator   
9286                     Tube, Utility, Clock Generator   
9287                     Tube, Utility, Clock Generator   
9288                    Dynamics, Effect, Tube, Utility   

                                              full_desc price_in_euro   
0     • 8 independent mono channels for audio signal...         ≈€260  \
1     • 8 independent mono channels for audio signal...         ≈€260   
2     • 8 independent mono channels for audio signal...         ≈€260   
3     • 8 independent mono channels for audio signal...         ≈€260   
4     The Orpho 8-Step is an eight-step sequencer wi...           €85   
...                                                 ...           ...   
9284  • eurorack format 2-digit counter of incoming ...         ≈€160   
9285  • eurorack format 2-digit counter of incoming ...         ≈€160   
9286  • eurorack format 2-digit counter of incoming ...         ≈€160   
9287  • eurorack format 2-digit counter of incoming ...         ≈€160   
9288                                                                    

     price_in_dollar                                         module_url   
0              ≈$289  https://modulargrid.net/e/paratek-%D0%A0%D0%98...  \
1              ≈$289  https://modulargrid.net/e/paratek-%D0%A0%D0%98...   

In [20]:
data.to_csv("scraped_data.csv", index = False)

In [21]:
data

id              module_name manufacturer   
0     24577     "РИТМИКС"  aluminium      Paratek  \
1     24578         "РИТМИКС"  black      Paratek   
2     26787         "РИТМИКС"  black      Paratek   
3     26788  "РИТМИКС"  black (pink)      Paratek   
4     29024                   8-Step        Orpho   
...     ...                      ...          ...   
9284  20853    ТАКТОМЕR-2c aluminium      Paratek   
9285  21301        ТАКТОМЕR-2c black      Paratek   
9286  20854              ТАКТОМЕR-2д      Paratek   
9287  21291        ТАКТОМЕR-2д black      Paratek   
9288  16926            Улучscheisseр       Svarog   

                        primary_desc  available  approved_stamp   
0              8 channels mixer unit          1               1  \
1              8 channels mixer unit          1               1   
2              8 channels mixer unit          1               1   
3              8 channels mixer unit          1               1   
4                  TRIGGER SEQUENCER          1               0   
...                              ...        ...             ...   
9284  Gate counter, clock, stopwatch          0               1   
9285  Gate counter, clock, stopwatch          0               1   
9286  Gate counter, clock, stopwatch          0               1   
9287  Gate counter, clock, stopwatch          0               1   
9288                то что вам надо!          0               0   

            physical_dim                          power_req   
0     12 HP | 38 mm deep   40 mA +12V | 5 mA -12V | ? mA 5V  \
1     12 HP | 38 mm deep   40 mA +12V | 5 mA -12V | ? mA 5V   
2     12 HP | 38 mm deep   40 mA +12V | 5 mA -12V | ? mA 5V   
3     12 HP | 38 mm deep   40 mA +12V | 5 mA -12V | ? mA 5V   
4      6 HP | 35 mm deep   50 mA +12V | ? mA -12V | ? mA 5V   
...                  ...                                ...   
9284   6 HP | 43 mm deep  180 mA +12V | 0 mA -12V | 0 mA 5V   
9285   6 HP | 43 mm deep  180 mA +12V | ? mA -12V | ? mA 5V   
9286   6 HP | 32 mm deep  180 mA +12V | 0 mA -12V | 0 mA 5V   
9287   6 HP | 32 mm deep  180 mA +12V | ? mA -12V | ? mA 5V   
9288   10 HP | 2 mm deep    ? mA +12V | ? mA -12V | ? mA 5V   

                                            module_tags   
0               Attenuator, Dual/Stereo, Mixer, Panning  \
1     Attenuator, Dual/Stereo, Mixer, Multiple, Panning   
2     Attenuator, Dual/Stereo, Mixer, Multiple, Panning   
3     Attenuator, Dual/Stereo, Mixer, Multiple, Panning   
4                                             Sequencer   
...                                                 ...   
9284                     Tube, Utility, Clock Generator   
9285                     Tube, Utility, Clock Generator   
9286                     Tube, Utility, Clock Generator   
9287                     Tube, Utility, Clock Generator   
9288                    Dynamics, Effect, Tube, Utility   

                                              full_desc price_in_euro   
0     • 8 independent mono channels for audio signal...         ≈€260  \
1     • 8 independent mono channels for audio signal...         ≈€260   
2     • 8 independent mono channels for audio signal...         ≈€260   
3     • 8 independent mono channels for audio signal...         ≈€260   
4     The Orpho 8-Step is an eight-step sequencer wi...           €85   
...                                                 ...           ...   
9284  • eurorack format 2-digit counter of incoming ...         ≈€160   
9285  • eurorack format 2-digit counter of incoming ...         ≈€160   
9286  • eurorack format 2-digit counter of incoming ...         ≈€160   
9287  • eurorack format 2-digit counter of incoming ...         ≈€160   
9288                                                                    

     price_in_dollar                                         module_url   
0              ≈$289  https://modulargrid.net/e/paratek-%D0%A0%D0%98...  \
1              ≈$289  https://modulargrid.net/e/paratek-%D0%A0%D0%98...   